In [2]:
# importing libraries
import numpy as np
import pandas as pd
import pydub

from IPython.display import Audio
from keras.layers import Dense, LSTM, LeakyReLU
from keras.models import Sequential, load_model
from scipy.io.wavfile import read, write

Using TensorFlow backend.


In [3]:
# converting mp3 file to wav file
sound = pydub.AudioSegment.from_mp3("/Volumes/S190813/Coding/BC_REPO/crystal-castles/i/04 - magic-spells.mp3")
sound.export("magic-spells.wav", format="wav")
sound = pydub.AudioSegment.from_mp3("/Volumes/S190813/Coding/BC_REPO/crystal-castles/i/03 - crimewave.mp3")
sound.export("crimewave.wav", format="wav")

<_io.BufferedRandom name='crimewave.wav'>

In [6]:
# loading the wav files
rate, music1 = read('magic-spells.wav')
rate, music2 = read('crimewave.wav')

In [14]:
# taking only some part of the songs and converting to a dataframe
music1 = pd.DataFrame(music1[0:400000, :])
music2 = pd.DataFrame(music2[0:400000, :])

In [15]:
# function to create train data by shifting the music data 
def create_train_dataset(df, look_back):
    dataX1, dataX2 , dataY1 , dataY2 = [],[],[],[]
    for i in range(len(df)-look_back-1):
        dataX1.append(df.iloc[i : i + look_back, 0].values)
        dataX2.append(df.iloc[i : i + look_back, 1].values)
        dataY1.append(df.iloc[i + look_back, 0])
        dataY2.append(df.iloc[i + look_back, 1])
    return np.array(dataX1), np.array(dataX2), np.array(dataY1), np.array(dataY2)

In [16]:
X1 , X2, y1 , y2 = create_train_dataset(pd.concat([music1.iloc[0 : 160000, :],music2.iloc[0 : 160000, :]], axis=0), 3)

In [17]:
print(X1.shape)
print(X2.shape)
print(y1.shape)
print(y2.shape)

(319996, 3)
(319996, 3)
(319996,)
(319996,)


In [18]:
# function to create train data by shifting the music data
def create_test_data(df, look_back):
    dataX1, dataX2 = [], []
    for i in range(len(df)-look_back-1):
        dataX1.append(df.iloc[i : i + look_back, 0].values)
        dataX2.append(df.iloc[i : i + look_back, 1].values)
        
    return np.array(dataX1), np.array(dataX2)

In [19]:
test1, test2 = create_test_data(pd.concat([music1.iloc[160001 : 400000, :],music2.iloc[160001 : 400000, :]], axis=0), 3)

In [91]:
test1

array([[ 4088,  4006,  3914],
       [ 4006,  3914,  3787],
       [ 3914,  3787,  3672],
       ...,
       [12443, 12685, 12639],
       [12685, 12639, 12405],
       [12639, 12405, 12068]], dtype=int16)

In [92]:
test3, test4 = create_test_data(pd.concat([music1.iloc[220001 : 400000, :],music2.iloc[220001 : 400000, :]], axis=0), 3)

In [20]:
X1 = X1.reshape((-1, 1, 3))
X2 = X2.reshape((-1, 1, 3))

In [21]:
# bad model
rnn_b1 = Sequential()
rnn_b1.add(LSTM(units=100, activation='relu', input_shape=(None, 3)))
rnn_b1.add(Dense(units=50, activation='relu'))
rnn_b1.add(Dense(units=25, activation='relu'))
rnn_b1.add(Dense(units=12, activation='relu'))
rnn_b1.add(Dense(units=1, activation='relu'))
rnn_b1.compile(optimizer='adam', loss='mean_squared_error')
rnn_b1.fit(X1, y1, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 27s 83us/step - loss: 4833539.7945
Epoch 2/20
319996/319996 [==============================] - 27s 84us/step - loss: 4794650.9172
Epoch 3/20
319996/319996 [==============================] - 26s 81us/step - loss: 4793763.7584
Epoch 4/20
319996/319996 [==============================] - 20s 61us/step - loss: 4793700.4175
Epoch 5/20
319996/319996 [==============================] - 20s 62us/step - loss: 4793035.3082
Epoch 6/20
319996/319996 [==============================] - 19s 60us/step - loss: 4792936.2933
Epoch 7/20
319996/319996 [==============================] - 20s 61us/step - loss: 4792858.7683
Epoch 8/20
319996/319996 [==============================] - 19s 60us/step - loss: 4792520.2997
Epoch 9/20
319996/319996 [==============================] - 19s 61us/step - loss: 4793138.5150
Epoch 10/20
319996/319996 [==============================] - 20s 64us/step - loss: 4792748.3169
Epoch 11/20
319996/319996 [======================

In [22]:
# bad model
rnn_b2 = Sequential()
rnn_b2.add(LSTM(units=100, activation='relu', input_shape=(None, 3)))
rnn_b2.add(Dense(units=50, activation='relu'))
rnn_b2.add(Dense(units=25, activation='relu'))
rnn_b2.add(Dense(units=12, activation='relu'))
rnn_b2.add(Dense(units=1, activation='relu'))
rnn_b2.compile(optimizer='adam', loss='mean_squared_error')
rnn_b2.fit(X2, y2, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 20s 63us/step - loss: 9497414.3127
Epoch 2/20
319996/319996 [==============================] - 21s 65us/step - loss: 9384738.3424
Epoch 3/20
319996/319996 [==============================] - 20s 61us/step - loss: 9383723.9179
Epoch 4/20
319996/319996 [==============================] - 21s 66us/step - loss: 9383750.3289
Epoch 5/20
319996/319996 [==============================] - 20s 63us/step - loss: 9382794.6858
Epoch 6/20
319996/319996 [==============================] - 20s 63us/step - loss: 9382608.4842
Epoch 7/20
319996/319996 [==============================] - 16s 51us/step - loss: 9382129.3953
Epoch 8/20
319996/319996 [==============================] - 18s 56us/step - loss: 9381255.6062
Epoch 9/20
319996/319996 [==============================] - 16s 50us/step - loss: 9381436.6846
Epoch 10/20
319996/319996 [==============================] - 18s 56us/step - loss: 9380791.5247
Epoch 11/20
319996/319996 [======================

In [24]:
rnn_b1.save('rnn_b1.h5')
rnn_b2.save('rnn_b2.h5')

In [26]:
rnn_b1 = load_model('rnn_b1.h5')
rnn_b2 = load_model('rnn_b2.h5')

In [27]:
# making bad predictions for channel 1 and channel 2
pred_rnn_b1 = rnn_b1.predict(test1.reshape(-1, 1, 3))
pred_rnn_b2 = rnn_b2.predict(test2.reshape(-1, 1, 3))

In [28]:
# bad output
write('bad_pred_rnn.wav', rate, pd.concat([pd.DataFrame(pred_rnn_b1.astype('int16')), pd.DataFrame(pred_rnn_b2.astype('int16'))], axis=1).values)

In [88]:
# worse model
rnn_b3 = Sequential()
rnn_b3.add(LSTM(units=1, activation='selu', input_shape=(None, 3)))
rnn_b3.compile(optimizer='SGD', loss='mean_squared_error')
rnn_b3.fit(X2, y2, epochs=20, batch_size=50)

Epoch 1/20
319996/319996 [==============================] - 24s 74us/step - loss: nan
Epoch 2/20
319996/319996 [==============================] - 19s 60us/step - loss: nan
Epoch 3/20
319996/319996 [==============================] - 18s 55us/step - loss: nan
Epoch 4/20
319996/319996 [==============================] - 22s 70us/step - loss: nan
Epoch 5/20
319996/319996 [==============================] - 23s 71us/step - loss: nan
Epoch 6/20
319996/319996 [==============================] - 19s 60us/step - loss: nan
Epoch 7/20
319996/319996 [==============================] - 21s 66us/step - loss: nan
Epoch 8/20
319996/319996 [==============================] - 16s 51us/step - loss: nan
Epoch 9/20
319996/319996 [==============================] - 21s 66us/step - loss: nan
Epoch 10/20
319996/319996 [==============================] - 20s 61us/step - loss: nan
Epoch 11/20
319996/319996 [==============================] - 19s 60us/step - loss: nan
Epoch 12/20
319996/319996 [=========================

In [89]:
rnn_b4 = Sequential()
rnn_b4.add(LSTM(units=1, activation='selu', input_shape=(None, 3)))
rnn_b4.compile(optimizer='SGD', loss='mean_squared_error')
rnn_b4.fit(X1, y1, epochs=20, batch_size=50)

Epoch 1/20
319996/319996 [==============================] - 32s 99us/step - loss: nan
Epoch 2/20
319996/319996 [==============================] - 19s 60us/step - loss: nan
Epoch 3/20
319996/319996 [==============================] - 19s 59us/step - loss: nan
Epoch 4/20
319996/319996 [==============================] - 21s 65us/step - loss: nan
Epoch 5/20
319996/319996 [==============================] - 20s 62us/step - loss: nan
Epoch 6/20
319996/319996 [==============================] - 20s 62us/step - loss: nan
Epoch 7/20
319996/319996 [==============================] - 31s 97us/step - loss: nan
Epoch 8/20
319996/319996 [==============================] - 26s 80us/step - loss: nan
Epoch 9/20
319996/319996 [==============================] - 21s 65us/step - loss: nan
Epoch 10/20
319996/319996 [==============================] - 20s 62us/step - loss: nan
Epoch 11/20
319996/319996 [==============================] - 20s 63us/step - loss: nan
Epoch 12/20
319996/319996 [=========================

In [90]:
rnn_b3.save('rnn_b3.h5')
rnn_b4.save('rnn_b4.h5')
rnn_b3 = load_model('rnn_b3.h5')
rnn_b4 = load_model('rnn_b4.h5')
pred_rnn_b3 = rnn_b3.predict(test1.reshape(-1, 1, 3))
pred_rnn_b4 = rnn_b4.predict(test2.reshape(-1, 1, 3))
write('worse_pred_rnn.wav', rate, pd.concat([pd.DataFrame(pred_rnn_b3.astype('int16')), pd.DataFrame(pred_rnn_b4.astype('int16'))], axis=1).values)

In [12]:
# LSTM Model for channel 1 of the music data
rnn1 = Sequential()
rnn1.add(LSTM(units=100, activation='linear', input_shape=(None, 3)))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=50, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=25, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=12, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=1, activation='linear'))
rnn1.add(LeakyReLU())

rnn1.compile(optimizer='adam', loss='mean_squared_error', metrics=['accuracy'])
rnn1.fit(X1, y1, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 19s 60us/step - loss: 265233.2003 - accuracy: 0.0094
Epoch 2/20
319996/319996 [==============================] - 18s 57us/step - loss: 158277.8700 - accuracy: 0.0090
Epoch 3/20
319996/319996 [==============================] - 19s 58us/step - loss: 157146.1679 - accuracy: 0.0082
Epoch 4/20
319996/319996 [==============================] - 18s 57us/step - loss: 155709.6657 - accuracy: 0.0079
Epoch 5/20
319996/319996 [==============================] - 19s 59us/step - loss: 156316.4910 - accuracy: 0.0076
Epoch 6/20
319996/319996 [==============================] - 19s 59us/step - loss: 156140.8363 - accuracy: 0.0078
Epoch 7/20
319996/319996 [==============================] - 19s 61us/step - loss: 157601.9483 - accuracy: 0.0072
Epoch 8/20
319996/319996 [==============================] - 19s 60us/step - loss: 155813.7477 - accuracy: 0.0072
Epoch 9/20
319996/319996 [==============================] - 19s 60us/step - loss: 155404.8941 - 

In [13]:
# LSTM Model for channel 2 of the music data
rnn2 = Sequential()
rnn2.add(LSTM(units=100, activation='linear', input_shape=(None, 3)))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=50, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=25, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=12, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=1, activation='linear'))
rnn2.add(LeakyReLU())

rnn2.compile(optimizer='adam', loss='mean_squared_error', metrics=['accuracy'])
rnn2.fit(X2, y2, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 19s 59us/step - loss: 387378.6438 - accuracy: 0.0077
Epoch 2/20
319996/319996 [==============================] - 19s 59us/step - loss: 194380.7837 - accuracy: 0.0077
Epoch 3/20
319996/319996 [==============================] - 19s 60us/step - loss: 190543.0064 - accuracy: 0.0075
Epoch 4/20
319996/319996 [==============================] - 20s 63us/step - loss: 190704.4025 - accuracy: 0.0075
Epoch 5/20
319996/319996 [==============================] - 19s 59us/step - loss: 189351.3451 - accuracy: 0.0069
Epoch 6/20
319996/319996 [==============================] - 19s 59us/step - loss: 187587.8898 - accuracy: 0.0073
Epoch 7/20
319996/319996 [==============================] - 19s 61us/step - loss: 188207.2303 - accuracy: 0.0071
Epoch 8/20
319996/319996 [==============================] - 19s 61us/step - loss: 186005.1962 - accuracy: 0.0070
Epoch 9/20
319996/319996 [==============================] - 20s 63us/step - loss: 185060.7449 - 

In [14]:
# saving LSTM models
rnn1.save('rnn1.h5')
rnn2.save('rnn2.h5')

In [94]:
# loading the saved models
rnn1 = load_model('rnn1.h5')
rnn2 = load_model('rnn2.h5')

In [16]:
# making predictions for channel 1 and channel 2
pred_rnn1 = rnn1.predict(test1.reshape(-1, 1, 3))
pred_rnn2 = rnn2.predict(test2.reshape(-1, 1, 3))

In [96]:
# making predictions for channel 1 and channel 2
alt_pred_rnn1 = rnn1.predict(test3.reshape(-1, 1, 3))
alt_pred_rnn2 = rnn2.predict(test4.reshape(-1, 1, 3))
# saving the LSTM predicitons in wav format
write('alt_pred_rnn.wav', rate, pd.concat([pd.DataFrame(alt_pred_rnn1.astype('int16')), pd.DataFrame(alt_pred_rnn2.astype('int16'))], axis=1).values)

In [17]:
# reshaping the data for input to ANN
X1 = X1.reshape((-1, 3))
X2 = X2.reshape((-1, 3))

In [18]:
# ANN Model for channel 1 of the music data
ann1 = Sequential()
ann1.add(Dense(units=100, activation='linear', input_dim=3))
ann1.add(LeakyReLU())
ann1.add(Dense(units=50, activation='linear'))
ann1.add(LeakyReLU())
ann1.add(Dense(units=25, activation='linear'))
ann1.add(LeakyReLU())
ann1.add(Dense(units=12, activation='linear'))
ann1.add(LeakyReLU())
ann1.add(Dense(units=1, activation='linear'))
ann1.add(LeakyReLU())

ann1.compile(optimizer='adam', loss='mean_squared_error', metrics=['accuracy'])
ann1.fit(X1, y1, epochs = 20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 9s 28us/step - loss: 204951.8743 - accuracy: 0.0093
Epoch 2/20
319996/319996 [==============================] - 9s 28us/step - loss: 156526.9309 - accuracy: 0.0093
Epoch 3/20
319996/319996 [==============================] - 7s 22us/step - loss: 155507.5457 - accuracy: 0.0091
Epoch 4/20
319996/319996 [==============================] - 7s 22us/step - loss: 154478.6809 - accuracy: 0.0090
Epoch 5/20
319996/319996 [==============================] - 7s 22us/step - loss: 153905.0923 - accuracy: 0.0092
Epoch 6/20
319996/319996 [==============================] - 9s 28us/step - loss: 153841.2192 - accuracy: 0.0086
Epoch 7/20
319996/319996 [==============================] - 8s 26us/step - loss: 153212.1527 - accuracy: 0.0084
Epoch 8/20
319996/319996 [==============================] - 7s 23us/step - loss: 153126.4580 - accuracy: 0.0085
Epoch 9/20
319996/319996 [==============================] - 7s 23us/step - loss: 152655.1104 - accuracy:

In [19]:
# ANN Model for channel 2 of the music data
ann2 = Sequential()
ann2.add(Dense(units=100, activation='linear', input_dim=3))
ann2.add(LeakyReLU())
ann2.add(Dense(units=50, activation='linear'))
ann2.add(LeakyReLU())
ann2.add(Dense(units=25, activation='linear'))
ann2.add(LeakyReLU())
ann2.add(Dense(units=12, activation='linear'))
ann2.add(LeakyReLU())
ann2.add(Dense(units=1, activation='linear'))
ann2.add(LeakyReLU())

ann2.compile(optimizer='adam', loss='mean_squared_error', metrics=['accuracy'])
ann2.fit(X2, y2, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 7s 23us/step - loss: 287143.3629 - accuracy: 0.0083
Epoch 2/20
319996/319996 [==============================] - 8s 26us/step - loss: 190457.4730 - accuracy: 0.0084
Epoch 3/20
319996/319996 [==============================] - 8s 24us/step - loss: 189198.2154 - accuracy: 0.0080
Epoch 4/20
319996/319996 [==============================] - 7s 22us/step - loss: 187539.1477 - accuracy: 0.0080
Epoch 5/20
319996/319996 [==============================] - 7s 22us/step - loss: 186413.9091 - accuracy: 0.0078
Epoch 6/20
319996/319996 [==============================] - 7s 23us/step - loss: 185706.0814 - accuracy: 0.0075
Epoch 7/20
319996/319996 [==============================] - 7s 23us/step - loss: 185967.4314 - accuracy: 0.0076
Epoch 8/20
319996/319996 [==============================] - 7s 23us/step - loss: 184918.5623 - accuracy: 0.0076
Epoch 9/20
319996/319996 [==============================] - 7s 23us/step - loss: 184466.8744 - accuracy:

In [20]:
# saving ANN models
ann1.save('ann1.h5')
ann2.save('ann2.h5')

In [21]:
# loading saved ANN models
ann1 = load_model('ann1.h5')
ann2 = load_model('ann2.h5')

In [22]:
# making predictions for channel 1 and channel 2
pred_ann1 = ann1.predict(test1)
pred_ann2 = ann2.predict(test2)

In [23]:
# saving the ANN predicitons in wav format
write('pred_ann.wav', rate, pd.concat([pd.DataFrame(pred_ann1.astype('int16')), pd.DataFrame(pred_ann2.astype('int16'))], axis=1).values)

In [24]:
# saving the LSTM predicitons in wav format
write('pred_rnn.wav', rate, pd.concat([pd.DataFrame(pred_rnn1.astype('int16')), pd.DataFrame(pred_rnn2.astype('int16'))], axis=1).values)

In [25]:
# saving the original music in wav format
write('original.wav',rate, pd.concat([music1.iloc[160001 : 400000, :], music2.iloc[160001 : 400000, :]], axis=0).values)

In [27]:
Audio("pred_ann.wav")

In [28]:
Audio("pred_rnn.wav")

In [29]:
Audio("original.wav")

Helping Jake

In [73]:
l = [1,4,6,5,6,7]
l_2 = [2,5,6,7,1]

In [74]:
lp = zip(l, l_2)

In [75]:
g = list(lp)

In [76]:
g

[(1, 2), (4, 5), (6, 6), (5, 7), (6, 1)]

In [67]:
sorted(g[0])

[1, 2]

In [77]:
sorted(g, key=lambda x: x[0])

[(1, 2), (4, 5), (5, 7), (6, 6), (6, 1)]